# Chapter 4: Statistical Data Analysis II - Parameter Estimation (Part 2)

## Practical fitting of models to data
Today, the evaluation of measurement data in the natural and engineering sciences is practically always carried out on a computer. However, some historical practices are still common today.

>**Straight line fitting in the past**:
>In earlier times, data, e.g., in physics laboratory, were often evaluated by hand. The data points were noted down on a sheet of paper or, better still, in a lab book and then plotted against each other on graph paper. A straight line was then drawn with a linear ruler and a sharp eye and its parameters read off the graph paper:
>
><img src="img/graph_paper.png" width="50%">



>**Straight line fitting using spreadsheets**
>Program packages for spreadsheets such as Microsoft Excel, Apple Numbers or OpenOffice Calc are widely used. They have a range of built-in functions for statistical analysis and graphical representation of tabulated data. These functions are **unsuitable** for most data analysis in physics laboratory courses and scientific research, especially when used with their default settings. The main problematic points are briefly described here using the example of a straight line fit in Excel:
>- We start from an Excel spreadsheet with data points $(x_i,y_i)$, where the $x_i$ are known exactly and the $y_i$ have an uncertainty $\sigma_i\equiv ey$. The data points were randomly generated from the linear function $y=0.3x+1$ with a relative uncertainty of $\sigma_i/y_i=0.1$.
>
>    x	| y	| ey 
>   ---|---|---
>   1.0|	1.24|	0.13
>   2.0|	1.60|	0.16
>   3.0|	1.70|	0.19
>   4.0|	1.95|	0.22
>   5.0|	2.26|	0.25
>   6.0|	3.21|	0.28
>   7.0|	3.13|	0.31
>   8.0|	3.10|	0.34
>   9.0|	3.39|	0.37
>   10.0|	4.32|	0.40
>
>
>- The first two columns of the table are selected and a scatter chart is inserted (tab *Insert*, *Scatter*). The data points are automatically connected with line segments, although no assumptions about $x$ values between the $x_i$ are known. These must first be switched off (select data points, select *No line* in the formatting menu).
>- Then we add the option for uncertainty bars (tab *Chart Design*, *Add Chart Element*, *Error Bars*, *More Error Bar Options*), select and delete the horizontal uncertainty bars and configure the vertical uncertainty bars (*Error Amount*, *Custom*, for positive and negative value select the column $ey$).
>- The straight line is created by selecting *Add Trend Line...* in the context menu of the data points. A straight line will then appear in the diagram, with *Display Equation on chart* the slope and intercept will also appear, but not their uncertainties. You can obtain further information on the trend line with *Display R-squared value on chart*. The definition of the coefficient of determination $R^2$ is discussed below.
>- Excel provides the function `LINEST` for linear regression with the LS method. This has an option to output further parameters of the fit (`Stats=True`): Parameter values (slope and $y$ intercept) and their uncertainties, coefficient of determination and dispersion of the $y$-values, F-statistics, number of degrees of freedom, sum of squares and residual sum of squares.
>
>The **coefficient of determination $R^2$** is used in many scientific disciplines to explain the quality of a model function. $R^2$ is a measure of what proportion of the scatter of the data $y_i$ is explained by the model $\lambda_i$ and what proportion remains unexplained. A high coefficient of determination indicates good agreement. For this purpose, the deviation of $y_i$ from its arithmetic mean $\overline{y}$ is divided into an explained and an unexplained part:
>$$
y_i - \overline{y} =
\underbrace{( \lambda_i - \overline{y} )}_{\textsf{explained}} +
\underbrace{( y_i - \lambda_i )}_{\textsf{unexplained}}.
>$$
>The coefficient of determination is then defined as
>$$
R^2 \equiv
\frac{\sum_i (\lambda_i - \overline{y})^2}{\sum_i (y_i - \overline{y})^2} =
 1 - \frac{\sum_i ( y_i - \lambda_i)^2}{\sum_i (y_i - \overline{y})^2}.
>$$
>The smaller the unexplained part is relative to the explained part, the closer the coefficient of determination is to one. If the model function is linear in the positions $x_i$, as in the case of the straight line, $R^2$ corresponds to the square of the correlation coefficient $\rho_{xy}$.
>
>Problematic points when using spreadsheet programs in data evaluation in physics include the following:
>- In terms of a well-controlled and documented **work flow**, this approach is clearly inferior to a Python script.
>- Spreadsheets "speak a different language" than parameter estimation in physics. The terminology may need to be translated.
>- In physics, data points are **always specified with uncertainties**. There is no way in Excel to include these uncertainties in the fit. This corresponds to the **ordinary least squares (OLS) method** without uncertainties (i.e., with $\sigma_i=1$), which is often assumed without a meaningful model of the uncertainties:
>$$
S_\mathsf{OLS} \equiv \sum_{i=1}^{n} (y_i - \lambda_i(x_i;\mathbf{a}))^2
\overset{!}{=}\mathsf{min}
>$$

### Goodness of fit: example
In the following code example, ten data points randomly generated from a linear function and their uncertainties are fitted to a straight line and a parabola. The $\chi^2$ probabilities are used as a measure of the goodness of fit to test which of the two different model functions (linear or quadratic) fits the data better and if the uncertainties were estimated correctly.

In [ ]:

"""Compare synthetic data from a linear model and fit to a linear and quadratic model"""
import numpy as np
import matplotlib.pyplot as plt 
from scipy.optimize import curve_fit
from scipy.stats import chi2

# range of values
n, xmin, xmax = 10, 1., 10.
xdata = np.linspace( xmin, xmax, n )

def lin_model( x, a0=1., a1=1. ):
	'''linear model (straight line)'''
	return a0 + a1*x
	
def quad_model( x, a0=1., a1=1., a2=1. ):
	'''quadratic model (parabola)'''
	return a0 + ( a1 + a2*x ) * x
	
def fit_model( func, name, ey, ax, abs_sigma=True ):
    """fit to synthetic data using scipy.optimize.curve_fit"""
	
    # perform the fit
	# Note: 
    popt, pcov = curve_fit( func, xdata, ydata, sigma=ey, absolute_sigma=abs_sigma )

    # compute residual sum of squares "manually"
    S = np.sum( ( ( ydata - func( xdata, *popt ) ) / ey  )**2 )
    ndof = n - len( popt ) # number of data points minus number of parameters
    prob = 1. - chi2.cdf( S, ndof )
    print( "Results using scipy.optimize.curve_fit (%s model)" % name )
    print( "  Parameters:                  ", popt )
    print( "  Uncertainties:               ", np.sqrt( np.diag(pcov) ) )
    print( "  Covariance matrix:\n", pcov )
    print( "  chi2, ndof, chi2/ndof, prob: ", S, ndof, S/ndof, prob )

    # plot
    ax.set_ylim( 0, 5 )
    ax.errorbar( xdata, ydata, yerr=ey, fmt='bo')
    ax.plot( xrange, func( xrange, *popt), 'r' ) 
    ax.text( 1, 4.5, "%s model:" % name )
    ax.text( 1, 4.25, r"$\chi^2/n_{\mathsf{dof}} = %4.2f/%d$" % (S, ndof))
    ax.text( 1, 4.0, r"$P_{\chi^2} = %4.2e$" % prob )
    if( func == lin_model ):
        ax.text( 1, 3.75, r"$\hat{a}_0 = %4.2f \pm %4.2f$" % ( popt[0], np.sqrt( pcov[0][0] ) ) )
        ax.text( 1, 3.5, r"$\hat{a}_1 = %4.2f \pm %4.2f$" % ( popt[1], np.sqrt( pcov[1][1] ) ) )

    return

# true parameter values
lin_model_pars  = [ 1.0, 0.3 ]

# relative uncertaintly of y values (assuming x values do not have uncertainties)
ey_rel = 0.1

# use hard-coded xy values according to this model directly
xrange = np.linspace( 0.5, 10.5, 200 )
xdata = np.array( [ 1.,  2.,  3.,  4. , 5.,  6. , 7.,  8.,  9., 10.] )
ydata = np.array( [ 1.23912799, 1.59626873, 1.69944363, 1.95397332, 2.26423559, 3.20817472, 3.12755677, 3.09552808, 3.39170581, 4.31564169 ] )


# fit and plot linear and quadratic model to four different uncertainty models
fig,ax = plt.subplots( 2, 4, figsize=(15,10))

# uncertainty model 1: 10% relative to true y value
ey1 = 0.1 * lin_model( xdata, *lin_model_pars ) 
fit_model( lin_model, "linear", ey1, ax[0][0] )
fit_model( quad_model, "quadratic", ey1, ax[1][0] )

# uncertainty model 2: all uncertainties divided by two
ey2 = 0.5*ey1
fit_model( lin_model, "linear", ey2, ax[0][1] )
fit_model( quad_model, "quadratic", ey2, ax[1][1] )

# uncertainty model 3: OLS fit aka the Excel way – all uncertainties = 1
ey3 = np.ones( n ) 
fit_model( lin_model, "linear", ey3, ax[0][2] )
fit_model( quad_model, "quadratic", ey3, ax[1][2] )

# uncertainty model 4: curve_fit default - scaling of covariance matrix for chi2/dof=1
ey4 = ey1
fit_model( lin_model, "linear", ey4, ax[0][3], False )
fit_model( quad_model, "quadratic", ey4, ax[1][3], False )

plt.show()


The four uncertainty models used in the above example and their influence on the quality of the fit are briefly discussed here:
1. Relative uncertainty of 10% of the true $y$-value. This model results in a $\chi^2$ probability of 59% for a linear function or a $\chi^2$ value of 6.53 for 8 degrees of freedom. This is close to $\chi^2/n_\mathsf{dof}=1$ and indicates a **good fit**. This can also be seen from the fact that eight or nine of the ten data points are compatible with the straight line within their uncertainties. For the usual (frequentist) interpretation of the uncertainty bars as 68.3% coverage of the true value by the confidence interval, this is expected for about seven data points.
For a quadratic function, the quality of the fit is of similar quality, with a slightly worse $\chi^2$ probability. Based on these criteria, it is not possible to decide which model function is the better one. Without further information, following [Occam's Razor](https://en.wikipedia.org/wiki/Occam%27s_razor) the model with **fewer parameters** should be selected, i.e., the linear model. If it were physically better motivated, the quadratic model could still be chosen.
1. Relative uncertainty of 5% of the true $y$-value. This model results in a $\chi^2$ probability of $10^{-3}$ or a $\chi^2$ value of 26.11 for 8 degrees of freedom for the linear function. The uncertainties are therefore **clearly too small**, seven data points are **not compatible with the straight line within the uncertainties**. The same applies to the quadratic model. It is also conceivable that the models are unsuitable; this cannot be decided without further knowledge of the data and model.
1. Ordinary (unweighted) linear regression, i.e. $\sigma_i=1$. You can see at first glance that all uncertainty bars are much too large, so that all data points are clearly compatible with the curve. This is also reflected in the $\chi^2$ probability of 1 and $\chi^2/n_\mathsf{dof}=0.56/8$. The **agreement is "too good "** and the uncertainty bars do not correspond to the usual 68.3% interpretation. As a result, the estimated uncertainties on the parameters are much too large and the parameter values shift slightly compared to the previous uncertainty models. This would have been the solution you would have gotten with tools like Excel - unusable for the physics laboratory course!
1. Relative uncertainty of 10% of the true $y$-value and default settings of `scipy.optimize.curve_fit` regarding the use of the uncertainties. The setting `absolute_sigma=False` means that the **absolute values of the uncertainties are ignored** and only the relative size of the uncertainties between the data points is used. The covariance matrix and thus all uncertainties are then scaled together so that $\chi^2/n_\mathsf{dof}=1$ is fulfilled. This is also reflected in the uncertainties of the model parameters, which are slightly smaller than in the first model. This may make sense if the uncertainty model is not exactly known, but in physics the uncertainty model is usually determined *before* fitting. This example shows that it is always important to pay attention to the "fine print" in the documentation of data analysis software.

### PhyPraKit and kafe2: Karlsruhe tools for parameter estimation
At the Institute of Experimental Particle Physics at KIT, software tools have been developed in recent years that are easy to use with previous knowledge of Python and correctly perform many standard tasks in physics laboratory courses. The package [`PhyPraKit`](https://etpwww.etp.kit.edu/~quast/PhyPraKit/htmldoc/) contains, among other things:
- Input and output of data with interfaces to the measuring devices used in the laboratory course.
- Digital signal processing: filtering for smoothing and searching for maxima and edges, FFT and autocorrelation.
- Statistical evaluation: mean values, covariance matrices, uncertainty propagation
- Working with histogrammed data
- Function fitting to data with the method of least squares and the maximum likelihood method and visualization, including correlated $x$ and $y$ uncertainties.
- Generation of synthetic data using the Monte Carlo method.

For function fitting, `PhyPraKit` internally uses the open-source package [`kafe2`](https://kafe2.readthedocs.io/en/latest/) (Karlsruhe Fit Environment), which makes current statistical methods accessible with a simple and fast interface and generates high-quality plots. There are several ways to work with `kafe2`:
- `PhyPraKit` provides easy-to-use functions that call `kafe2` methods.
- Comparably easy to use are the wrapper functions that `kafe2` itself provides for its most important methods.
- `kafe2` can also be called as a standalone program on the command line (`kafe2go`), whereby it is configured via YAML files.

>**Recommendation**: We recommend the use of `PhyPraKit` and `kafe2` for the physics laboratory course at KIT. Some of the functionality of these programs can also be easily achieved in Python with NumPy and Scipy (or with other software packages) - all previous example programs show this. Other things are only possible with some additional effort, e.g., the correct treatment of correlated $x$ and $y$ uncertainties.

The example of a straight line fit is now to be carried out in a code example with `kafe2`. This package has wrapper functions for adjustments (`kafe2.xy_fit()`) and their graphical representation (`kafe2.plot()`), which are used to call the underlying methods. The package `PhyPraKit` for the physics laboratory course also contains a simple interface to these methods (`PhyPraKit.k2Fit()`), but this is only available for reasons of compatibility with earlier versions.  
 
In the code example, a straight line for determining an electrical resistance $R$ or the conductance $G=1/R$ is to be determined. For this purpose, the measured voltages $V$ and currents $I$ are read in from a CSV file and fitted with Ohm's law in the forms $I = GV$ and $I=V/R$ and alternatively with a linear function with two parameters $I=GV+I_0$. The comparison of the models with one and two parameters shows that $I_0$ is compatible with zero and only leads to a greater uncertainty on $G$. Ohm's law is therefore preferred as the simplest model for describing the data.

A useful feature of `kafe2` for a clear visualization of function fits are the uncertainty bands around the function graph. These show the envelope of the maximum permissible variation of the model parameters within the uncertainties.

In [ ]:
"""Using PhyPraKit for a straight line fit in the laboratory course: Ohm's law as an example"""

#magic command needed to display plots inline
%matplotlib ipympl

import numpy as np
import matplotlib.pyplot as plt 
import kafe2
from PhyPraKit import k2Fit

def ohm_model_G( V, G=1. ):
	'''Ohm's Law using conductance'''
	return G*V

def ohm_model_R( V, R=1. ):
	'''Ohm's Law using resistance'''
	return V/R

def lin_model( V, G=1., I0=0. ):
	'''linear model (straight line)'''
	return G*V + I0
	
# absolute uncertainties in x and y
ex, ey = 0.015, 0.015

# read data from CSV file
data = np.genfromtxt('data/DataOhmsLaw.csv', delimiter=",", skip_header=3 )
V, I = data[:,0], data[:,1]
labels = [ r"$V$ (V)", r"$I$ (A)" ]

# straight line fit: use kafe2 wrapper function xy_fit() for fitting and plot() plotting
# Note: without setting save=False, a file with fit results would be saved

# fit to Ohm's law with conductance G
result_ohm_G = kafe2.xy_fit( ohm_model_G, V, I, x_error=ex, y_error=ey, save=False )
kafe2.plot( x_label=labels[0], y_label=labels[1], save=False )

# fit to Ohm's law with resistance R
result_ohm_R = kafe2.xy_fit( ohm_model_R, V, I, x_error=ex, y_error=ey, save=False )
kafe2.plot( x_label=labels[0], y_label=labels[1], save=False )

# fit to linear model with additional current I0
result_lin = kafe2.xy_fit( lin_model, V, I, x_error=ex, y_error=ey, save=False )
kafe2.plot( x_label=labels[0], y_label=labels[1], save=False )
print( result_lin )

# legacy code for backwards compatibility using PhyPraKit.k2Fit()
#par, pare, corr, S = k2Fit( ohm_model_G, V, I, sx=ex, sy=ey, axis_labels=labels )
#par, pare, corr, S = k2Fit( ohm_model_R, V, I, sx=ex, sy=ey, axis_labels=labels )
#par, pare, corr, S = k2Fit( lin_model, V, I, sx=ex, sy=ey, axis_labels=labels )
#print( par, pare, corr, S )